In [ ]:
import spacy

# Load the English NLP model
nlp = spacy.load("en_core_web_sm")

def extract_item_name(sentence):
    doc = nlp(sentence)
    possible_items = []

    for chunk in doc.noun_chunks:
        filtered_tokens = [token.text for token in chunk if not (token.pos_ in ["DET", "NUM"])]

        if any(tok.pos_ in ["NOUN", "PROPN"] for tok in chunk):
            possible_items.append(" ".join(filtered_tokens))

    if possible_items:
        return max(possible_items, key=len)

    return None

# Example usage
sentence = "Can I get one Chicken Katsu Curry with extra rice?"
item_name = extract_item_name(sentence)
print(f"Extracted item name: {item_name}")

: 

# **1. Installation of Required Libraries**

In [2]:
# %pip install transformers datasets torch scikit-learn -q
# %pip install transformers[torch] -q
# %pip install accelerate -U -q

# **2. Implementation Code**

In [3]:
import torch
from datasets import load_dataset
from transformers import AutoTokenizer, AutoModelForSequenceClassification, Trainer, TrainingArguments
from sklearn.metrics import accuracy_score, precision_recall_fscore_support

/home/ig-420/Igenerate/Huggingface code/order_bot/env/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [4]:
import pandas as pd
from sklearn.model_selection import train_test_split
import torch
from torch import nn
from transformers import AutoTokenizer, AutoModelForSequenceClassification

In [5]:
dataset = pd.read_excel("fine_tune_dataset.xlsx")

In [6]:
dataset.head(5)

Sentence Operation Item Name  \
0                          Add 3 bananas to my cart.       add   bananas   
1                 Can you put 5 oranges in the cart?       add   oranges   
2     Please remove 1 pack of cookies from the cart.    remove   cookies   
3  I need to update the cart with 4 bottles of milk.    update      milk   
4               Take 2 bags of chips out of my cart.    remove     chips   

  Quantity  
0        3  
1        5  
2        1  
3        4  
4        2

In [7]:
# dataset = load_dataset("imdb")
model_name = "distilbert-base-uncased"
tokenizer = AutoTokenizer.from_pretrained(model_name)

/home/ig-420/Igenerate/Huggingface code/order_bot/env/lib/python3.11/site-packages/transformers/tokenization_utils_base.py:1617: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be deprecated in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


In [8]:
# device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
device = torch.device("mps" if torch.backends.mps.is_available() else "cpu")

In [9]:
device

device(type='cpu')

In [10]:
dataset['tokenized'] = dataset['Sentence'].apply(lambda x: tokenizer(x, padding='max_length', truncation=True, return_tensors="pt"))


In [11]:
dataset.tail(5)

Sentence Operation Item Name Quantity  \
644      What is currently in my shopping cart?      view      none     none   
645                        Please show my cart.      view      none     none   
646  Can I see the current contents of my cart?      view      none     none   
647           Could you show me my cart status?      view      none     none   
648    What are the items in my cart right now?      view      none     none   

                       tokenized  
644  [input_ids, attention_mask]  
645  [input_ids, attention_mask]  
646  [input_ids, attention_mask]  
647  [input_ids, attention_mask]  
648  [input_ids, attention_mask]

In [12]:
operation_mapping = {'add': 0, 'remove': 1, 'update': 2, 'view': 3}
dataset['Operation_Label'] = dataset['Operation'].map(operation_mapping)

In [13]:
train_operation_df, test_operation_df = train_test_split(dataset[['Sentence', 'Operation']], test_size=0.2, random_state=42)

train_quantity_df, test_quantity_df = train_test_split(dataset[['Sentence', 'Quantity']], test_size=0.2, random_state=42)


In [14]:
# Operation classification model (3 labels: add, remove, update)
operation_model = AutoModelForSequenceClassification.from_pretrained(model_name, num_labels=len(operation_mapping))
operation_model.to(device)

# Quantity classification model (for simplicity, assuming up to 20 distinct quantities)
quantity_model = AutoModelForSequenceClassification.from_pretrained(model_name, num_labels=20)
quantity_model.to(device)

Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight', 'pre_classifier.bias', 'pre_classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight', 'pre_classifier.bias', 'pre_classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


DistilBertForSequenceClassification(
  (distilbert): DistilBertModel(
    (embeddings): Embeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (transformer): Transformer(
      (layer): ModuleList(
        (0-5): 6 x TransformerBlock(
          (attention): MultiHeadSelfAttention(
            (dropout): Dropout(p=0.1, inplace=False)
            (q_lin): Linear(in_features=768, out_features=768, bias=True)
            (k_lin): Linear(in_features=768, out_features=768, bias=True)
            (v_lin): Linear(in_features=768, out_features=768, bias=True)
            (out_lin): Linear(in_features=768, out_features=768, bias=True)
          )
          (sa_layer_norm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
          (ffn): FFN(
            (dropout): Dropout(p=0.1, inplace=False)
 

In [15]:
from transformers import Trainer, TrainingArguments

# Training arguments
training_args = TrainingArguments(
    output_dir="./results",
    evaluation_strategy="epoch",
    save_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=10,
    weight_decay=0.01,
    logging_dir='./logs',
    logging_steps=10,
    load_best_model_at_end=True,
    save_total_limit=2,
    save_steps=500,
)

/home/ig-420/Igenerate/Huggingface code/order_bot/env/lib/python3.11/site-packages/transformers/training_args.py:1545: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [16]:
from sklearn.metrics import accuracy_score, precision_recall_fscore_support

In [17]:
def compute_metrics(pred):
    labels = pred.label_ids
    preds = pred.predictions.argmax(-1)
    precision, recall, f1, _ = precision_recall_fscore_support(labels, preds, average='weighted')
    acc = accuracy_score(labels, preds)
    return {
        'accuracy': acc,
        'f1': f1,
        'precision': precision,
        'recall': recall
    }

In [18]:
# Define the mapping from operation strings to integer labels
operation_label_mapping = {
    "add": 0,
    "remove": 1,
    "update": 2,
    "view": 3
}

# Apply the mapping to the dataset
train_operation_df["Operation_Label"] = train_operation_df["Operation"].map(operation_label_mapping)
test_operation_df["Operation_Label"] = test_operation_df["Operation"].map(operation_label_mapping)


In [19]:
class CustomDataset(torch.utils.data.Dataset):
    def __init__(self, df, tokenizer, max_length=128):
        self.df = df
        self.tokenizer = tokenizer
        self.max_length = max_length

    def __len__(self):
        return len(self.df)

    def __getitem__(self, idx):
        # Ensure the idx is within the correct range
        if torch.is_tensor(idx):
            idx = idx.tolist()

        # Fetch the row by index
        sentence = self.df.iloc[idx]["Sentence"]
        operation_label = self.df.iloc[idx]["Operation_Label"]  # Use the integer label now

        # Tokenize the sentence
        encoding = self.tokenizer(
            sentence,
            padding="max_length",
            truncation=True,
            max_length=self.max_length,
            return_tensors="pt"
        )

        # Create a dictionary with input data and label
        item = {
            "input_ids": encoding["input_ids"].squeeze(),
            "attention_mask": encoding["attention_mask"].squeeze(),
            "labels": torch.tensor(operation_label, dtype=torch.long)  # Use the integer label
        }

        return item


In [20]:
train_dataset = CustomDataset(train_operation_df, tokenizer)
test_dataset = CustomDataset(test_operation_df, tokenizer)

In [21]:
operation_trainer = Trainer(
    model=operation_model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=test_dataset,
    compute_metrics=compute_metrics
)

# Train the model
operation_trainer.train()

# Evaluate the model
eval_results = operation_trainer.evaluate()
print(f"Evaluation Results: {eval_results}")

# Save the model
operation_model.save_pretrained("./fine-tuned-operation-model")
tokenizer.save_pretrained("./fine-tuned-operation-model")

  3%|▎         | 10/330 [02:19<1:15:04, 14.08s/it]

{'loss': 1.3225, 'grad_norm': 2.9805526733398438, 'learning_rate': 1.9393939393939395e-05, 'epoch': 0.3}


  6%|▌         | 20/330 [05:32<1:51:00, 21.49s/it]

{'loss': 1.0513, 'grad_norm': 4.0864691734313965, 'learning_rate': 1.8787878787878792e-05, 'epoch': 0.61}


  9%|▉         | 30/330 [09:31<2:03:13, 24.65s/it]

...

100%|██████████| 330/330 [2:26:57<00:00, 26.72s/it]


{'train_runtime': 8817.7112, 'train_samples_per_second': 0.589, 'train_steps_per_second': 0.037, 'train_loss': 0.15002734196005446, 'epoch': 10.0}


100%|██████████| 9/9 [00:21<00:00,  2.40s/it]


Evaluation Results: {'eval_loss': 0.007898399606347084, 'eval_accuracy': 1.0, 'eval_f1': 1.0, 'eval_precision': 1.0, 'eval_recall': 1.0, 'eval_runtime': 24.4138, 'eval_samples_per_second': 5.325, 'eval_steps_per_second': 0.369, 'epoch': 10.0}


('./fine-tuned-operation-model/tokenizer_config.json',
 './fine-tuned-operation-model/special_tokens_map.json',
 './fine-tuned-operation-model/vocab.txt',
 './fine-tuned-operation-model/added_tokens.json',
 './fine-tuned-operation-model/tokenizer.json')

In [22]:
import torch
from torch.utils.data import Dataset

class QuantityDataset(Dataset):
    def __init__(self, df, tokenizer, max_length=128):
        self.df = df
        self.tokenizer = tokenizer
        self.max_length = max_length

    def __len__(self):
        return len(self.df)

    def __getitem__(self, idx):
        # Ensure the idx is within the correct range
        if torch.is_tensor(idx):
            idx = idx.tolist()

        # Fetch the row by index
        sentence = self.df.iloc[idx]["Sentence"]
        quantity_label = self.df.iloc[idx]["Quantity"]  # Use the integer label now

        # Tokenize the sentence
        encoding = self.tokenizer(
            sentence,
            padding="max_length",
            truncation=True,
            max_length=self.max_length,
            return_tensors="pt"
        )

        # Create a dictionary with input data and label
        item = {
            "input_ids": encoding["input_ids"].squeeze(),
            "attention_mask": encoding["attention_mask"].squeeze(),
            "labels": torch.tensor(quantity_label, dtype=torch.long)  # Use the integer label
        }

        return item


In [23]:
# Replace NaN in 'quantity' column with 0
train_quantity_df['Quantity'] = pd.to_numeric(train_quantity_df['Quantity'], errors='coerce').fillna(0)
test_quantity_df['Quantity'] = pd.to_numeric(test_quantity_df['Quantity'], errors='coerce').fillna(0)

# train_quantity_df["Quantity"] = train_quantity_df['Quantity'].fillna(0)
# test_quantity_df["Quantity"] = test_quantity_df['Quantity'].fillna(0)

In [24]:
train_quantity_df["Quantity"] = train_quantity_df["Quantity"].astype(int)
test_quantity_df["Quantity"] = test_quantity_df["Quantity"].astype(int)

# Create a CustomDataset for the quantity model
train_quantity_dataset = QuantityDataset(train_quantity_df, tokenizer)
test_quantity_dataset = QuantityDataset(test_quantity_df, tokenizer)

In [25]:
quantity_trainer = Trainer(
    model=quantity_model,  # The model for quantities (numeric prediction)
    args=training_args,
    train_dataset=train_quantity_dataset,  # Training dataset for quantity
    eval_dataset=test_quantity_dataset,  # Evaluation dataset for quantity
    compute_metrics=compute_metrics
)

# Train the quantity model
quantity_trainer.train()

# Evaluate the quantity model on the test dataset
eval_results_quantity = quantity_trainer.evaluate(eval_dataset=test_quantity_dataset)
print(f"Evaluation Results for Quantity Model: {eval_results_quantity}")

# Save the trained quantity model and tokenizer
quantity_model.save_pretrained("./fine-tuned-quantity-model")
tokenizer.save_pretrained("./fine-tuned-quantity-model")

  3%|▎         | 10/330 [01:41<51:54,  9.73s/it] 

{'loss': 2.9295, 'grad_norm': 3.623546600341797, 'learning_rate': 1.9393939393939395e-05, 'epoch': 0.3}


  6%|▌         | 20/330 [03:47<1:04:11, 12.43s/it]

{'loss': 2.7411, 'grad_norm': 3.69571852684021, 'learning_rate': 1.8787878787878792e-05, 'epoch': 0.61}


  9%|▉         | 30/330 [06:17<1:12:06, 14.42s/it]

...

100%|██████████| 330/330 [1:26:17<00:00, 15.69s/it]


{'train_runtime': 5177.7572, 'train_samples_per_second': 1.002, 'train_steps_per_second': 0.064, 'train_loss': 1.0024475039857808, 'epoch': 10.0}


100%|██████████| 9/9 [00:34<00:00,  3.79s/it]


Evaluation Results for Quantity Model: {'eval_loss': 0.17457057535648346, 'eval_accuracy': 1.0, 'eval_f1': 1.0, 'eval_precision': 1.0, 'eval_recall': 1.0, 'eval_runtime': 38.991, 'eval_samples_per_second': 3.334, 'eval_steps_per_second': 0.231, 'epoch': 10.0}


('./fine-tuned-quantity-model/tokenizer_config.json',
 './fine-tuned-quantity-model/special_tokens_map.json',
 './fine-tuned-quantity-model/vocab.txt',
 './fine-tuned-quantity-model/added_tokens.json',
 './fine-tuned-quantity-model/tokenizer.json')

# **3. Using the Model for Prediction**


In [26]:
import spacy
from transformers import AutoTokenizer, AutoModelForSequenceClassification

nlp = spacy.load("en_core_web_sm")

In [27]:
operation_model_name = "./fine-tuned-operation-model"
quantity_model_name = "./fine-tuned-quantity-model"

operation_tokenizer = AutoTokenizer.from_pretrained(operation_model_name)
quantity_tokenizer = AutoTokenizer.from_pretrained(quantity_model_name)

operation_model = AutoModelForSequenceClassification.from_pretrained(operation_model_name)
quantity_model = AutoModelForSequenceClassification.from_pretrained(quantity_model_name)

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
operation_model.to(device)
quantity_model.to(device)

DistilBertForSequenceClassification(
  (distilbert): DistilBertModel(
    (embeddings): Embeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (transformer): Transformer(
      (layer): ModuleList(
        (0-5): 6 x TransformerBlock(
          (attention): MultiHeadSelfAttention(
            (dropout): Dropout(p=0.1, inplace=False)
            (q_lin): Linear(in_features=768, out_features=768, bias=True)
            (k_lin): Linear(in_features=768, out_features=768, bias=True)
            (v_lin): Linear(in_features=768, out_features=768, bias=True)
            (out_lin): Linear(in_features=768, out_features=768, bias=True)
          )
          (sa_layer_norm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
          (ffn): FFN(
            (dropout): Dropout(p=0.1, inplace=False)
 

In [28]:
def predict_operation(sentence):
    inputs = operation_tokenizer(sentence, padding=True, truncation=True, return_tensors="pt").to(device)
    with torch.no_grad():
        outputs = operation_model(**inputs)
    logits = outputs.logits
    predictions = torch.softmax(logits, dim=-1)
    predicted_label = torch.argmax(predictions, dim=-1).item()
    operation = "Add" if predicted_label == 0 else "Remove"  # Adjust based on your label encoding
    return operation, predictions[0].cpu().numpy()

def predict_quantity(sentence):
    inputs = quantity_tokenizer(sentence, padding=True, truncation=True, return_tensors="pt").to(device)
    with torch.no_grad():
        outputs = quantity_model(**inputs)
    logits = outputs.logits
    predictions = torch.softmax(logits, dim=-1)
    predicted_quantity = torch.argmax(predictions, dim=-1).item()
    return predicted_quantity, predictions[0].cpu().numpy()

def extract_item_name(sentence):
    doc = nlp(sentence)
    noun_chunks = [chunk.text for chunk in doc.noun_chunks]
    for chunk in noun_chunks:
        if any(tok.pos_ == "NOUN" for tok in nlp(chunk).doc):
            return chunk

    return None

In [29]:
sentence = "Add soups to my cart."

# Predict operation and quantity
operation, operation_probs = predict_operation(sentence)
quantity, quantity_probs = predict_quantity(sentence)

print(f"Sentence: {sentence}")
print(f"Predicted Operation: {operation}")
print(f"Operation Probabilities: {operation_probs}")

print(f"Predicted Quantity: {quantity}")
print(f"Quantity Probabilities: {quantity_probs}")

print(f"Item Name -----> {extract_item_name(sentence=sentence)}")

Sentence: Add soups to my cart.
Predicted Operation: Add
Operation Probabilities: [0.9962047  0.00111221 0.00120974 0.00147345]
Predicted Quantity: 1
Quantity Probabilities: [0.07971817 0.2707245  0.1223022  0.11824853 0.03780839 0.09126952
 0.06610113 0.05348995 0.03518798 0.02410132 0.02650298 0.00751828
 0.01491447 0.00636614 0.00600904 0.00775851 0.00745718 0.00924029
 0.00832553 0.00695582]
Item Name -----> soups
